# 1. Install Required Packages

In [1]:
!pip install ultralytics
!pip install opencv-python

  Using cached opencv_python-4.10.0.84-cp37-abi3-win_amd64.whl.metadata (20 kB)
  Using cached tqdm-4.66.5-py3-none-any.whl.metadata (57 kB)
  Using cached py_cpuinfo-9.0.0-py3-none-any.whl.metadata (794 bytes)
  Using cached seaborn-0.13.2-py3-none-any.whl.metadata (5.4 kB)
  Using cached cycler-0.12.1-py3-none-any.whl.metadata (3.8 kB)
  Using cached pyparsing-3.1.4-py3-none-any.whl.metadata (5.1 kB)
  Using cached tzdata-2024.1-py2.py3-none-any.whl.metadata (1.4 kB)
  Using cached mpmath-1.3.0-py3-none-any.whl.metadata (8.6 kB)
   ---------------------------------------- 0.0/873.6 kB ? eta -:--:--
   --------------------------------------- 873.6/873.6 kB 19.1 MB/s eta 0:00:00
   ---------------------------------------- 0.0/7.8 MB ? eta -:--:--
   ----------------------------- ---------- 5.8/7.8 MB 35.3 MB/s eta 0:00:01
   ---------------------------------------- 7.8/7.8 MB 26.9 MB/s eta 0:00:00
   ---------------------------------------- 0.0/15.8 MB ? eta -:--:--
   ----------------

In [1]:
#Make sure your Python Version is 3.9, otherwise YOLO might not work correctly

import sys
print("Python Version:", sys.version)

Python Version: 3.9.19 (main, May  6 2024, 20:12:36) [MSC v.1916 64 bit (AMD64)]


# 2. Imports

In [1]:
from ultralytics import YOLO, solutions
import cv2

# 3. Vehicle Counting


## 3.1 Choose Model

In [2]:
model = YOLO("03_Models/YOLOv10-B.pt")
#model = YOLO("03_Models/YOLOv10-B_Trained.pt")
#model = YOLO("03_Models/YOLOv10-B_Trained_Preprocessed.pt")

## 3.2 Counting

### 3.2.1 2023-12-08_07-19_MaVI13.avi

In [3]:
video = cv2.VideoCapture('05_Videos/2023-12-08_07-19_MaVI13.avi')
assert video.isOpened(), "Error reading video file"

AssertionError: Error reading video file

In [4]:
text_color = (255,255,255)

#Define counts for each class and lane
cars_count_l = 0
transporter_count_l = 0
truck_count_l = 0
motorcycle_count_l = 0

cars_count_r = 0
transporter_count_r = 0
truck_count_r = 0
motorcycle_count_r = 0

#Define start and endpoint of video
w, h, fps = (int(video.get(x)) for x in (cv2.CAP_PROP_FRAME_WIDTH, cv2.CAP_PROP_FRAME_HEIGHT, cv2.CAP_PROP_FPS))

start = 1127
end = 6507

start_frame = start * fps
video.set(cv2.CAP_PROP_POS_FRAMES, start_frame)

end_frame = end * fps

# Define line points
line_points_r = [(40, 170), (175, 145)]
line_points_l = [(176, 145), (268, 125)]

classes_to_count = [0, 1, 2, 3]

# Video writer
video_writer = cv2.VideoWriter("05_Videos/o2023-12-08_07-19_MaVI13_Base.avi", cv2.VideoWriter_fourcc(*"mp4v"), fps, (w, h))

# Init Object Counters
counter_r = solutions.ObjectCounter(
    view_img=True,
    reg_pts=line_points_r ,
    names=model.names,
    draw_tracks=True,
    line_thickness=1,
    count_reg_color = (255,0,0),
    view_out_counts = False,
    view_in_counts = False
)

counter_l = solutions.ObjectCounter(
    view_img=True,
    reg_pts=line_points_l,
    names=model.names,
    draw_tracks=True,
    line_thickness=2,
    count_reg_color = (0,255,0),
    view_out_counts = False,
    view_in_counts = False
)

#Vehicle counting
while video.isOpened():

    #Check if end of video is reached
    current_frame_number = int(video.get(cv2.CAP_PROP_POS_FRAMES))
    print(current_frame_number)
    if (current_frame_number > end_frame):
        break

    #Read current frame
    success, im0 = video.read()
    if not success:
        print("Video frame is empty or video processing has been successfully completed.")
        break
    

    #Vehicle tracking & counting
    tracks = model.track(im0, persist=True, show=False, classes = classes_to_count, tracker = "bytetrack.yaml")

    count_results_l = counter_l.class_wise_count
    count_results_r = counter_r.class_wise_count

    im0 = counter_r.start_counting(im0, tracks)
    im0 = counter_l.start_counting(im0, tracks)

    #Create counting overlay
    overlay = im0.copy()
    cv2.rectangle(overlay, (15,24), (210,78), (0, 0, 0), -1)
    cv2.addWeighted(overlay, 0.7, im0, 0.3, 0, im0)
    
    if 'car' in counter_l.class_wise_count:
        cars_count_l = counter_l.class_wise_count["car"]["IN"] + counter_l.class_wise_count["car"]["OUT"]
    if 'transporter' in counter_l.class_wise_count:    
        transporter_count_l = counter_l.class_wise_count["transporter"]["IN"] + counter_l.class_wise_count["transporter"]["OUT"]
    if 'truck' in counter_l.class_wise_count:
        truck_count_l = counter_l.class_wise_count["truck"]["IN"] + counter_l.class_wise_count["truck"]["OUT"]
    if 'motorcycle' in counter_l.class_wise_count:
        motorcycle_count_l = counter_l.class_wise_count["motorcycle"]["IN"] + counter_l.class_wise_count["motorcycle"]["OUT"]
    
    cv2.putText(im0,str(f"Left Lane"),(15,34),cv2.FONT_HERSHEY_SIMPLEX, 0.3, text_color, 1, cv2.LINE_AA)
    cv2.putText(im0,str(f"Cars: {cars_count_l}"),(15,44),cv2.FONT_HERSHEY_SIMPLEX, 0.3, text_color, 1, cv2.LINE_AA) 
    cv2.putText(im0,str(f"Transporters: {transporter_count_l}"),(15,54),cv2.FONT_HERSHEY_SIMPLEX, 0.3, text_color, 1, cv2.LINE_AA) 
    cv2.putText(im0,str(f"Trucks: {truck_count_l}"),(15,64),cv2.FONT_HERSHEY_SIMPLEX, 0.3, text_color, 1, cv2.LINE_AA) 
    cv2.putText(im0,str(f"Motorcycles: {motorcycle_count_l}"),(15,74),cv2.FONT_HERSHEY_SIMPLEX, 0.3, text_color, 1, cv2.LINE_AA) 

    if 'car' in counter_r.class_wise_count:
        cars_count_r = counter_r.class_wise_count["car"]["IN"] + counter_r.class_wise_count["car"]["OUT"]
    if 'transporter' in counter_r.class_wise_count:    
        transporter_count_r = counter_r.class_wise_count["transporter"]["IN"] + counter_r.class_wise_count["transporter"]["OUT"]
    if 'truck' in counter_r.class_wise_count:
        truck_count_r = counter_r.class_wise_count["truck"]["IN"] + counter_r.class_wise_count["truck"]["OUT"]
    if 'motorcycle' in counter_r.class_wise_count:
        motorcycle_count_r = counter_r.class_wise_count["motorcycle"]["IN"] + counter_r.class_wise_count["motorcycle"]["OUT"]
    
    cv2.putText(im0,str(f"Right Lane"),(110,34),cv2.FONT_HERSHEY_SIMPLEX, 0.3, text_color, 1, cv2.LINE_AA) 
    cv2.putText(im0,str(f"Cars: {cars_count_r}"),(110,44),cv2.FONT_HERSHEY_SIMPLEX, 0.3, text_color, 1, cv2.LINE_AA) 
    cv2.putText(im0,str(f"Transporters: {transporter_count_r}"),(110,54),cv2.FONT_HERSHEY_SIMPLEX, 0.3, text_color, 1, cv2.LINE_AA) 
    cv2.putText(im0,str(f"Trucks: {truck_count_r}"),(110,64),cv2.FONT_HERSHEY_SIMPLEX, 0.3, text_color, 1, cv2.LINE_AA) 
    cv2.putText(im0,str(f"Motorcycles: {motorcycle_count_r}"),(110,74),cv2.FONT_HERSHEY_SIMPLEX, 0.3, text_color, 1, cv2.LINE_AA) 

    
    video_writer.write(im0)

video_writer.release()
cv2.destroyAllWindows()

Line Counter Initiated.
Line Counter Initiated.


In [ ]:
print(counter_r.class_wise_count)
print(counter_l.class_wise_count)

### 3.2.2 2024-04-09_15-55_MaVI4.avi

In [29]:
video = cv2.VideoCapture('05_Videos/2024-04-09_15-55_MaVI4.avi')
assert video.isOpened(), "Error reading video file"

In [ ]:
text_color = (255,255,255)

#Define counts for each class and lane
cars_count = 0
transporter_count = 0
truck_count = 0
motorcycle_count = 0

#Define start and endpoint of video
w, h, fps = (int(video.get(x)) for x in (cv2.CAP_PROP_FRAME_WIDTH, cv2.CAP_PROP_FRAME_HEIGHT, cv2.CAP_PROP_FPS))

start = 298
end = 3898

start_frame = start * fps
video.set(cv2.CAP_PROP_POS_FRAMES, start_frame)

end_frame = end * fps

# Define line points
line_points = [(145, 160), (235, 115)]

classes_to_count = [0, 1, 2, 3]

# Video writer
video_writer = cv2.VideoWriter("05_Videos/2024-04-09_15-55_MaVI4_Base.avi", cv2.VideoWriter_fourcc(*"mp4v"), fps, (w, h))

# Init Object Counters
counter = solutions.ObjectCounter(
    view_img=True,
    reg_pts=line_points,
    names=model.names,
    draw_tracks=True,
    line_thickness=2,
    view_out_counts = False,
    view_in_counts = False
)

#Vehicle counting
while video.isOpened():

    #Check if end of video is reached
    current_frame_number = int(video.get(cv2.CAP_PROP_POS_FRAMES))
    print(current_frame_number)
    if (current_frame_number > end_frame):
        break

    #Read current frame
    success, im0 = video.read()
    if not success:
        print("Video frame is empty or video processing has been successfully completed.")
        break
    
    #Vehicle tracking & counting
    tracks = model.track(im0, persist=True, show=False, classes = classes_to_count, tracker = "bytetrack.yaml")

    count_results = counter.class_wise_count

    im0 = counter.start_counting(im0, tracks)

    #Create counting overlay
    overlay = im0.copy()
    cv2.rectangle(overlay, (15,24), (150,78), (0, 0, 0), -1)
    cv2.addWeighted(overlay, 0.7, im0, 0.3, 0, im0)
    
    if 'car' in counter.class_wise_count:
        cars_count = counter.class_wise_count["car"]["IN"] + counter.class_wise_count["car"]["OUT"]
    if 'transporter' in counter.class_wise_count:    
        transporter_count = counter.class_wise_count["transporter"]["IN"] + counter.class_wise_count["transporter"]["OUT"]
    if 'truck' in counter.class_wise_count:
        truck_count = counter.class_wise_count["truck"]["IN"] + counter.class_wise_count["truck"]["OUT"]
    if 'motorcycle' in counter.class_wise_count:
        motorcycle_count = counter.class_wise_count["motorcycle"]["IN"] + counter.class_wise_count["motorcycle"]["OUT"]
    
    cv2.putText(im0,str(f"Left Lane"),(15,34),cv2.FONT_HERSHEY_SIMPLEX, 0.3, text_color, 1, cv2.LINE_AA)
    cv2.putText(im0,str(f"Cars: {cars_count}"),(15,44),cv2.FONT_HERSHEY_SIMPLEX, 0.3, text_color, 1, cv2.LINE_AA) 
    cv2.putText(im0,str(f"Transporters: {transporter_count}"),(15,54),cv2.FONT_HERSHEY_SIMPLEX, 0.3, text_color, 1, cv2.LINE_AA) 
    cv2.putText(im0,str(f"Trucks: {truck_count}"),(15,64),cv2.FONT_HERSHEY_SIMPLEX, 0.3, text_color, 1, cv2.LINE_AA) 
    cv2.putText(im0,str(f"Motorcycles: {motorcycle_count}"),(15,74),cv2.FONT_HERSHEY_SIMPLEX, 0.3, text_color, 1, cv2.LINE_AA) 
    
    video_writer.write(im0)

video_writer.release()
cv2.destroyAllWindows()

Line Counter Initiated.
4470

0: 544x640 3 cars, 389.0ms
Speed: 3.0ms preprocess, 389.0ms inference, 0.0ms postprocess per image at shape (1, 3, 544, 640)
4471

0: 544x640 3 cars, 344.0ms
Speed: 3.0ms preprocess, 344.0ms inference, 0.0ms postprocess per image at shape (1, 3, 544, 640)
4472

0: 544x640 3 cars, 339.0ms
Speed: 3.0ms preprocess, 339.0ms inference, 0.0ms postprocess per image at shape (1, 3, 544, 640)
4473

0: 544x640 3 cars, 352.0ms
Speed: 3.0ms preprocess, 352.0ms inference, 0.0ms postprocess per image at shape (1, 3, 544, 640)
4474

0: 544x640 3 cars, 449.0ms
Speed: 3.0ms preprocess, 449.0ms inference, 1.0ms postprocess per image at shape (1, 3, 544, 640)
4475

0: 544x640 4 cars, 353.0ms
Speed: 3.0ms preprocess, 353.0ms inference, 0.0ms postprocess per image at shape (1, 3, 544, 640)
4476

0: 544x640 2 cars, 330.0ms
Speed: 3.0ms preprocess, 330.0ms inference, 1.0ms postprocess per image at shape (1, 3, 544, 640)
4477

0: 544x640 3 cars, 340.0ms
Speed: 2.0ms preprocess, 3

In [ ]:
print(counter.class_wise_count)

### 3.2.3 2024-04-11_07-55_MaVI5.avi

In [ ]:
video = cv2.VideoCapture('05_Videos/2024-04-11_07-55_MaVI5.avi')
assert video.isOpened(), "Error reading video file"

In [ ]:
text_color = (255,255,255)

#Define counts for each class and lane
cars_count_l = 0
transporter_count_l = 0
truck_count_l = 0
motorcycle_count_l = 0

cars_count_r = 0
transporter_count_r = 0
truck_count_r = 0
motorcycle_count_r = 0

#Define start and endpoint of video
w, h, fps = (int(video.get(x)) for x in (cv2.CAP_PROP_FRAME_WIDTH, cv2.CAP_PROP_FRAME_HEIGHT, cv2.CAP_PROP_FPS))

start = 300
end = 3885

start_frame = start * fps
video.set(cv2.CAP_PROP_POS_FRAMES, start_frame)

end_frame = end * fps

# Define line points
line_points_r = [(15, 210), (155, 255)]
line_points_l = [(156, 255), (315, 225)]

classes_to_count = [0, 1, 2, 3]

# Video writer
video_writer = cv2.VideoWriter("05_Videos/o2023-12-08_07-19_MaVI5_Base.avi", cv2.VideoWriter_fourcc(*"mp4v"), fps, (w, h))

# Init Object Counters
counter_r = solutions.ObjectCounter(
    view_img=True,
    reg_pts=line_points_r ,
    names=model.names,
    draw_tracks=True,
    line_thickness=1,
    count_reg_color = (255,0,0),
    view_out_counts = False,
    view_in_counts = False
)

counter_l = solutions.ObjectCounter(
    view_img=True,
    reg_pts=line_points_l,
    names=model.names,
    draw_tracks=True,
    line_thickness=2,
    count_reg_color = (0,255,0),
    view_out_counts = False,
    view_in_counts = False
)

#Vehicle counting
while video.isOpened():

    #Check if end of video is reached
    current_frame_number = int(video.get(cv2.CAP_PROP_POS_FRAMES))
    print(current_frame_number)
    if (current_frame_number > end_frame):
        break

    #Read current frame
    success, im0 = video.read()
    if not success:
        print("Video frame is empty or video processing has been successfully completed.")
        break

    #Vehicle tracking & counting
    tracks = model.track(im0, persist=True, show=False, classes = classes_to_count, tracker = "bytetrack.yaml")

    count_results_l = counter_l.class_wise_count
    count_results_r = counter_r.class_wise_count
    
    im0 = counter_r.start_counting(im0, tracks)
    im0 = counter_l.start_counting(im0, tracks)

    #Create counting overlay
    overlay = im0.copy()
    cv2.rectangle(overlay, (15,24), (210,78), (0, 0, 0), -1)
    cv2.addWeighted(overlay, 0.7, im0, 0.3, 0, im0)
    
    if 'car' in counter_l.class_wise_count:
        cars_count_l = counter_l.class_wise_count["car"]["IN"] + counter_l.class_wise_count["car"]["OUT"]
    if 'transporter' in counter_l.class_wise_count:    
        transporter_count_l = counter_l.class_wise_count["transporter"]["IN"] + counter_l.class_wise_count["transporter"]["OUT"]
    if 'truck' in counter_l.class_wise_count:
        truck_count_l = counter_l.class_wise_count["truck"]["IN"] + counter_l.class_wise_count["truck"]["OUT"]
    if 'motorcycle' in counter_l.class_wise_count:
        motorcycle_count_l = counter_l.class_wise_count["motorcycle"]["IN"] + counter_l.class_wise_count["motorcycle"]["OUT"]
    
    cv2.putText(im0,str(f"Left Lane"),(15,34),cv2.FONT_HERSHEY_SIMPLEX, 0.3, text_color, 1, cv2.LINE_AA)
    cv2.putText(im0,str(f"Cars: {cars_count_l}"),(15,44),cv2.FONT_HERSHEY_SIMPLEX, 0.3, text_color, 1, cv2.LINE_AA) 
    cv2.putText(im0,str(f"Transporters: {transporter_count_l}"),(15,54),cv2.FONT_HERSHEY_SIMPLEX, 0.3, text_color, 1, cv2.LINE_AA) 
    cv2.putText(im0,str(f"Trucks: {truck_count_l}"),(15,64),cv2.FONT_HERSHEY_SIMPLEX, 0.3, text_color, 1, cv2.LINE_AA) 
    cv2.putText(im0,str(f"Motorcycles: {motorcycle_count_l}"),(15,74),cv2.FONT_HERSHEY_SIMPLEX, 0.3, text_color, 1, cv2.LINE_AA) 

    if 'car' in counter_r.class_wise_count:
        cars_count_r = counter_r.class_wise_count["car"]["IN"] + counter_r.class_wise_count["car"]["OUT"]
    if 'transporter' in counter_r.class_wise_count:    
        transporter_count_r = counter_r.class_wise_count["transporter"]["IN"] + counter_r.class_wise_count["transporter"]["OUT"]
    if 'truck' in counter_r.class_wise_count:
        truck_count_r = counter_r.class_wise_count["truck"]["IN"] + counter_r.class_wise_count["truck"]["OUT"]
    if 'motorcycle' in counter_r.class_wise_count:
        motorcycle_count_r = counter_r.class_wise_count["motorcycle"]["IN"] + counter_r.class_wise_count["motorcycle"]["OUT"]
    
    cv2.putText(im0,str(f"Right Lane"),(110,34),cv2.FONT_HERSHEY_SIMPLEX, 0.3, text_color, 1, cv2.LINE_AA) 
    cv2.putText(im0,str(f"Cars: {cars_count_r}"),(110,44),cv2.FONT_HERSHEY_SIMPLEX, 0.3, text_color, 1, cv2.LINE_AA) 
    cv2.putText(im0,str(f"Transporters: {transporter_count_r}"),(110,54),cv2.FONT_HERSHEY_SIMPLEX, 0.3, text_color, 1, cv2.LINE_AA) 
    cv2.putText(im0,str(f"Trucks: {truck_count_r}"),(110,64),cv2.FONT_HERSHEY_SIMPLEX, 0.3, text_color, 1, cv2.LINE_AA) 
    cv2.putText(im0,str(f"Motorcycles: {motorcycle_count_r}"),(110,74),cv2.FONT_HERSHEY_SIMPLEX, 0.3, text_color, 1, cv2.LINE_AA) 

    video_writer.write(im0)
    
video_writer.release()
cv2.destroyAllWindows()

0: 544x640 (no detections), 320.5ms
Speed: 2.0ms preprocess, 320.5ms inference, 0.0ms postprocess per image at shape (1, 3, 544, 640)
5063

0: 544x640 1 person, 318.0ms
Speed: 4.0ms preprocess, 318.0ms inference, 0.0ms postprocess per image at shape (1, 3, 544, 640)
5064

0: 544x640 (no detections), 347.0ms
Speed: 2.0ms preprocess, 347.0ms inference, 1.0ms postprocess per image at shape (1, 3, 544, 640)
5065

0: 544x640 1 person, 346.0ms
Speed: 3.0ms preprocess, 346.0ms inference, 1.0ms postprocess per image at shape (1, 3, 544, 640)
5066

0: 544x640 1 person, 308.0ms
Speed: 3.0ms preprocess, 308.0ms inference, 0.0ms postprocess per image at shape (1, 3, 544, 640)
5067

0: 544x640 1 person, 324.0ms
Speed: 2.0ms preprocess, 324.0ms inference, 1.0ms postprocess per image at shape (1, 3, 544, 640)
5068

0: 544x640 1 person, 309.0ms
Speed: 2.0ms preprocess, 309.0ms inference, 0.0ms postprocess per image at shape (1, 3, 544, 640)
5069

0: 544x640 1 person, 350.0ms
Speed: 2.0ms preprocess, 3

In [ ]:
print(counter_r.class_wise_count)
print(counter_l.class_wise_count)

### 3.2.4 2024-04-10_19-55_MaVI18.avi

In [ ]:
video = cv2.VideoCapture('05_Videos/2024-04-10_19-55_MaVI18.avi')
assert video.isOpened(), "Error reading video file"

In [ ]:
text_color = (255,255,255)

#Define counts for each class and lane
cars_count_l = 0
transporter_count_l = 0
truck_count_l = 0
motorcycle_count_l = 0

cars_count_r = 0
transporter_count_r = 0
truck_count_r = 0
motorcycle_count_r = 0


#Define start and endpoint of video
w, h, fps = (int(video.get(x)) for x in (cv2.CAP_PROP_FRAME_WIDTH, cv2.CAP_PROP_FRAME_HEIGHT, cv2.CAP_PROP_FPS))

start = 300
end = 3885

start_frame = start * fps
video.set(cv2.CAP_PROP_POS_FRAMES, start_frame)

end_frame = end * fps

# Define line points
line_points_r = [(63, 176), (145, 220)]
line_points_l = [(205, 168), (285, 130)]

classes_to_count = [0, 1, 2, 3]

# Video writer
video_writer = cv2.VideoWriter("05_Videos/o2023-12-08_07-19_MaVI18_Base.avi", cv2.VideoWriter_fourcc(*"mp4v"), fps, (w, h))

# Init Object Counters
counter_r = solutions.ObjectCounter(
    view_img=True,
    reg_pts=line_points_r ,
    names=model.names,
    draw_tracks=True,
    line_thickness=1,
    count_reg_color = (255,0,0),
    view_out_counts = False,
    view_in_counts = False
)

counter_l = solutions.ObjectCounter(
    view_img=True,
    reg_pts=line_points_l,
    names=model.names,
    draw_tracks=True,
    line_thickness=2,
    count_reg_color = (0,255,0),
    view_out_counts = False,
    view_in_counts = False
)

#Vehicle counting
while video.isOpened():

    #Check if end of video is reached
    current_frame_number = int(video.get(cv2.CAP_PROP_POS_FRAMES))
    print(current_frame_number)
    if (current_frame_number > end_frame):
        break

    #Read current frame
    success, im0 = video.read()
    if not success:
        print("Video frame is empty or video processing has been successfully completed.")
        break
    
    #Vehicle tracking & counting
    tracks = model.track(im0, persist=True, show=False, classes = classes_to_count, tracker = "bytetrack.yaml")

    count_results_l = counter_l.class_wise_count
    count_results_r = counter_r.class_wise_count
    
    im0 = counter_r.start_counting(im0, tracks)
    im0 = counter_l.start_counting(im0, tracks)

    #Create counting overlay
    overlay = im0.copy()
    cv2.rectangle(overlay, (15,24), (210,78), (0, 0, 0), -1)
    cv2.addWeighted(overlay, 0.7, im0, 0.3, 0, im0)

    #Add counts to video
    if 'car' in counter_l.class_wise_count:
        cars_count_l = counter_l.class_wise_count["car"]["IN"] + counter_l.class_wise_count["car"]["OUT"]
    if 'transporter' in counter_l.class_wise_count:    
        transporter_count_l = counter_l.class_wise_count["transporter"]["IN"] + counter_l.class_wise_count["transporter"]["OUT"]
    if 'truck' in counter_l.class_wise_count:
        truck_count_l = counter_l.class_wise_count["truck"]["IN"] + counter_l.class_wise_count["truck"]["OUT"]
    if 'motorcycle' in counter_l.class_wise_count:
        motorcycle_count_l = counter_l.class_wise_count["motorcycle"]["IN"] + counter_l.class_wise_count["motorcycle"]["OUT"]
    
    cv2.putText(im0,str(f"Left Lane"),(15,34),cv2.FONT_HERSHEY_SIMPLEX, 0.3, text_color, 1, cv2.LINE_AA)
    cv2.putText(im0,str(f"Cars: {cars_count_l}"),(15,44),cv2.FONT_HERSHEY_SIMPLEX, 0.3, text_color, 1, cv2.LINE_AA) 
    cv2.putText(im0,str(f"Transporters: {transporter_count_l}"),(15,54),cv2.FONT_HERSHEY_SIMPLEX, 0.3, text_color, 1, cv2.LINE_AA) 
    cv2.putText(im0,str(f"Trucks: {truck_count_l}"),(15,64),cv2.FONT_HERSHEY_SIMPLEX, 0.3, text_color, 1, cv2.LINE_AA) 
    cv2.putText(im0,str(f"Motorcycles: {motorcycle_count_l}"),(15,74),cv2.FONT_HERSHEY_SIMPLEX, 0.3, text_color, 1, cv2.LINE_AA) 

    if 'car' in counter_r.class_wise_count:
        cars_count_r = counter_r.class_wise_count["car"]["IN"] + counter_r.class_wise_count["car"]["OUT"]
    if 'transporter' in counter_r.class_wise_count:    
        transporter_count_r = counter_r.class_wise_count["transporter"]["IN"] + counter_r.class_wise_count["transporter"]["OUT"]
    if 'truck' in counter_r.class_wise_count:
        truck_count_r = counter_r.class_wise_count["truck"]["IN"] + counter_r.class_wise_count["truck"]["OUT"]
    if 'motorcycle' in counter_r.class_wise_count:
        motorcycle_count_r = counter_r.class_wise_count["motorcycle"]["IN"] + counter_r.class_wise_count["motorcycle"]["OUT"]
    
    cv2.putText(im0,str(f"Right Lane"),(110,34),cv2.FONT_HERSHEY_SIMPLEX, 0.3, text_color, 1, cv2.LINE_AA) 
    cv2.putText(im0,str(f"Cars: {cars_count_r}"),(110,44),cv2.FONT_HERSHEY_SIMPLEX, 0.3, text_color, 1, cv2.LINE_AA) 
    cv2.putText(im0,str(f"Transporters: {transporter_count_r}"),(110,54),cv2.FONT_HERSHEY_SIMPLEX, 0.3, text_color, 1, cv2.LINE_AA) 
    cv2.putText(im0,str(f"Trucks: {truck_count_r}"),(110,64),cv2.FONT_HERSHEY_SIMPLEX, 0.3, text_color, 1, cv2.LINE_AA) 
    cv2.putText(im0,str(f"Motorcycles: {motorcycle_count_r}"),(110,74),cv2.FONT_HERSHEY_SIMPLEX, 0.3, text_color, 1, cv2.LINE_AA) 
    
    video_writer.write(im0)

video_writer.release()
cv2.destroyAllWindows()

0: 544x640 1 person, 309.0ms
Speed: 2.0ms preprocess, 309.0ms inference, 0.0ms postprocess per image at shape (1, 3, 544, 640)
5065

0: 544x640 2 persons, 306.0ms
Speed: 2.0ms preprocess, 306.0ms inference, 0.0ms postprocess per image at shape (1, 3, 544, 640)
5066

0: 544x640 2 persons, 358.0ms
Speed: 2.0ms preprocess, 358.0ms inference, 0.0ms postprocess per image at shape (1, 3, 544, 640)
5067

0: 544x640 2 persons, 350.0ms
Speed: 3.0ms preprocess, 350.0ms inference, 0.0ms postprocess per image at shape (1, 3, 544, 640)
5068

0: 544x640 2 persons, 346.0ms
Speed: 2.0ms preprocess, 346.0ms inference, 1.0ms postprocess per image at shape (1, 3, 544, 640)
5069

0: 544x640 2 persons, 313.0ms
Speed: 3.0ms preprocess, 313.0ms inference, 0.0ms postprocess per image at shape (1, 3, 544, 640)
5070

0: 544x640 2 persons, 327.0ms
Speed: 2.0ms preprocess, 327.0ms inference, 1.0ms postprocess per image at shape (1, 3, 544, 640)
5071

0: 544x640 2 persons, 363.0ms
Speed: 3.0ms preprocess, 363.0ms 

In [ ]:
print(counter_r.class_wise_count)
print(counter_l.class_wise_count)

### 3.2.5 Sanity Check

In [7]:
video = cv2.VideoCapture('05_Videos/Additional/SanityCheck.mp4')
assert video.isOpened(), "Error reading video file"

In [10]:
text_color = (255,255,255)

#Define counts for each class and lane
cars_count = 0
transporter_count = 0
truck_count = 0
motorcycle_count = 0

#Define start and endpoint of video
w, h, fps = (int(video.get(x)) for x in (cv2.CAP_PROP_FRAME_WIDTH, cv2.CAP_PROP_FRAME_HEIGHT, cv2.CAP_PROP_FPS))

start = 0
end = 3898

start_frame = start * fps
video.set(cv2.CAP_PROP_POS_FRAMES, start_frame)

end_frame = end * fps

# Define line points
line_points = [(270, 583), (1280, 583)]

classes_to_count = [0, 1, 2, 3]

# Video writer
video_writer = cv2.VideoWriter("05_Videos/SanityCheck.avi", cv2.VideoWriter_fourcc(*"mp4v"), fps, (w, h))

# Init Object Counters
counter = solutions.ObjectCounter(
    view_img=True,
    reg_pts=line_points,
    names=model.names,
    draw_tracks=True,
    line_thickness=2,
    view_out_counts = False,
    view_in_counts = False
)

#Vehicle counting
while video.isOpened():

    #Check if end of video is reached
    current_frame_number = int(video.get(cv2.CAP_PROP_POS_FRAMES))
    print(current_frame_number)
    if (current_frame_number > end_frame):
        break

    #Read current frame
    success, im0 = video.read()
    if not success:
        print("Video frame is empty or video processing has been successfully completed.")
        break
    
    #Vehicle tracking & counting
    tracks = model.track(im0, persist=True, show=False, classes = classes_to_count, tracker = "bytetrack.yaml")

    count_results = counter.class_wise_count

    im0 = counter.start_counting(im0, tracks)

    #Create counting overlay
    overlay = im0.copy()
    cv2.rectangle(overlay, (15,24), (150,78), (0, 0, 0), -1)
    cv2.addWeighted(overlay, 0.7, im0, 0.3, 0, im0)
    
    if 'car' in counter.class_wise_count:
        cars_count = counter.class_wise_count["car"]["IN"] + counter.class_wise_count["car"]["OUT"]
    if 'transporter' in counter.class_wise_count:    
        transporter_count = counter.class_wise_count["transporter"]["IN"] + counter.class_wise_count["transporter"]["OUT"]
    if 'truck' in counter.class_wise_count:
        truck_count = counter.class_wise_count["truck"]["IN"] + counter.class_wise_count["truck"]["OUT"]
    if 'motorcycle' in counter.class_wise_count:
        motorcycle_count = counter.class_wise_count["motorcycle"]["IN"] + counter.class_wise_count["motorcycle"]["OUT"]
    
    cv2.putText(im0,str(f"Left Lane"),(15,34),cv2.FONT_HERSHEY_SIMPLEX, 0.3, text_color, 1, cv2.LINE_AA)
    cv2.putText(im0,str(f"Cars: {cars_count}"),(15,44),cv2.FONT_HERSHEY_SIMPLEX, 0.3, text_color, 1, cv2.LINE_AA) 
    cv2.putText(im0,str(f"Transporters: {transporter_count}"),(15,54),cv2.FONT_HERSHEY_SIMPLEX, 0.3, text_color, 1, cv2.LINE_AA) 
    cv2.putText(im0,str(f"Trucks: {truck_count}"),(15,64),cv2.FONT_HERSHEY_SIMPLEX, 0.3, text_color, 1, cv2.LINE_AA) 
    cv2.putText(im0,str(f"Motorcycles: {motorcycle_count}"),(15,74),cv2.FONT_HERSHEY_SIMPLEX, 0.3, text_color, 1, cv2.LINE_AA) 
    
    video_writer.write(im0)

video_writer.release()
cv2.destroyAllWindows()

Line Counter Initiated.
0

0: 384x640 1 person, 4 cars, 223.0ms
Speed: 2.0ms preprocess, 223.0ms inference, 0.0ms postprocess per image at shape (1, 3, 384, 640)
1

0: 384x640 4 cars, 225.0ms
Speed: 1.0ms preprocess, 225.0ms inference, 0.0ms postprocess per image at shape (1, 3, 384, 640)
2

0: 384x640 4 cars, 245.0ms
Speed: 1.0ms preprocess, 245.0ms inference, 0.0ms postprocess per image at shape (1, 3, 384, 640)
3

0: 384x640 4 cars, 265.0ms
Speed: 2.0ms preprocess, 265.0ms inference, 1.0ms postprocess per image at shape (1, 3, 384, 640)
4

0: 384x640 4 cars, 234.0ms
Speed: 1.0ms preprocess, 234.0ms inference, 0.0ms postprocess per image at shape (1, 3, 384, 640)
5

0: 384x640 4 cars, 223.0ms
Speed: 2.0ms preprocess, 223.0ms inference, 1.0ms postprocess per image at shape (1, 3, 384, 640)
6

0: 384x640 4 cars, 220.0ms
Speed: 2.0ms preprocess, 220.0ms inference, 1.0ms postprocess per image at shape (1, 3, 384, 640)
7

0: 384x640 4 cars, 225.0ms
Speed: 1.0ms preprocess, 225.0ms inferen